import numpy as np
import pandas as pd
# ^^^ pyforest auto-imports - don't write above this line
# Time Series modelling - y only - calculating rmse

In [110]:
import pandas as pd
import numpy as np

# ^^^ pyforest auto-imports - don't write above this line


from sklearn.model_selection import TimeSeriesSplit
from scipy import stats
import statsmodels.api as sm
from sklearn.metrics import mean_squared_error


In [111]:
#Loading in combined train and test set

df = pd.read_csv('train.csv')
df_test = pd.read_csv('test.csv')

df["train_test"] = 'train'
df_test["train_test"] = "test"

df_combined = pd.concat([df,df_test])

/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:9: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  if __name__ == '__main__':


In [112]:
#Linear interpolation on all features

def interpolator(df):
    for g in df.galaxy.unique():
        #splitting out the individual galaxies
        df_temp = df[df['galaxy']==g].copy()
        df = df[~(df['galaxy']==g)]
        #filling the Nans (first with interpolation and then backfilling if missing for start)
        df_temp.sort_values("galactic year",inplace=True)
        df_temp.interpolate(method='linear',inplace=True)
        df_temp.fillna(method ='bfill',inplace=True)
        df_temp.fillna(method ='ffill',inplace=True)
        #adding back to dataframe
        df = pd.concat([df,df_temp])
    #filling the Nans for any which didnt have anything to fill at all
    df.fillna(df.mean(),inplace=True)
    return df

df_combined = interpolator(df_combined)
#df_combined = pd.get_dummies(df_combined, columns=['galaxy'])
df = df_combined[df_combined["train_test"]=='train'].copy()
df_test = df_combined[df_combined["train_test"]=='test'].copy()
df.drop('train_test',axis=1,inplace=True)
df_test.drop('train_test',axis=1,inplace=True)


In [113]:
#Fitting galactic year to date time format

df['galactic year 1'] = df['galactic year'].apply(lambda x:(np.round((x/1000),0))*2)
df['galactic year 1'] = df['galactic year 1'].astype('int64')
df['galactic year 1'] = df['galactic year 1'].astype('str')
df['galactic year 1'] = df['galactic year 1'] + "0101"
df['date'] = pd.to_datetime(df['galactic year 1'], yearfirst=True
                                 , format='%Y/%m/%d'
                                )
df.head()

Adjusted net savings   \
0                43.391708   
194              43.391708   
410              43.391708   
543              43.391708   
765              43.391708   

     Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
0                                           174.617899                      
194                                         165.945907                      
410                                         157.273915                      
543                                         148.601923                      
765                                         139.929931                      

     Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
0                                             6.313144                           
194                                           6.313144                           
410                                           6.313144                           
543                                           6.313144                           
765                                           6.313144                           

     Current health expenditure (% of GGP)  \
0                                 6.248891   
194                               6.248891   
410                               6.248891   
543                               6.248891   
765                               6.248891   

     Domestic credit provided by financial sector (% of GGP)  Education Index  \
0                                            75.604799               0.526375   
194                                          73.837393               0.526375   
410                                          72.069987               0.526375   
543                                          70.302580               0.526375   
765                                          68.535174               0.526375   

     Employment in agriculture (% of total employment)  \
0                                            96.827657   
194                                          96.827657   
410                                          95.022335   
543                                          93.217014   
765                                          91.411692   

     Employment in services (% of total employment)  \
0                                         53.392606   
194                                       53.392606   
410                                       50.937661   
543                                       48.482717   
765                                       46.027772   

     Employment to population ratio (% ages 15 and older)  \
0                                            76.506783      
194                                          76.506783      
410                                          76.302787      
543                                          76.098791      
765                                          75.894795      

     Estimated gross galactic income per capita, female  ...  \
0                                         16498.415777   ...   
194                                       16498.415777   ...   
410                                       16498.415777   ...   
543                                       16498.415777   ...   
765                                       16498.415777   ...   

     Vulnerable employment (% of total employment)  \
0                                        91.911151   
194                                      91.911151   
410                                      93.217778   
543                                      94.524405   
765                                      95.831032   

     Young age (0-14) dependency ratio (per 100 creatures ages 15-64)  \
0                                            98.216072                  
194                                          95.964868                  
410                                          93.713664                  
543                                          91.462460 

In [54]:
#Testing on one galaxy

split_1_y = []
split_2_y = []
split_0_y = []
split_1_preds = []
split_2_preds = []
split_0_preds = []


for g in df.galaxy.unique()[:1]:
    
    print(g)
    df_temp = df[df['galaxy']==g].copy()
    
    df_temp.sort_values("galactic year 1",inplace=True)
#             df_temp['galactic year'] = df_temp['galactic year'].apply(lambda x:(np.round((x/1000),0))*2)
#             df_temp['galactic year'] = df_temp['galactic year'].astype('int64')
#             df_temp['galactic year'] = df_temp['galactic year'].astype('str')
#             df_temp['galactic year'] = df_temp['galactic year'] + "0101"
#             df_temp['date'] = pd.to_datetime(df_temp['galactic year'], yearfirst=True
#                                              , format='%Y/%m/%d'
#                                             )

    df_temp_temp = df_temp[['date','y','galaxy','galactic year 1']]
    df_temp_temp_1 = df_temp_temp[['date','y']].copy()
    df_temp_temp_1.set_index('date', inplace=True, drop=True)
    data = df_temp_temp_1
    

    ts = TimeSeriesSplit(n_splits=3)
    splits = [split for split in ts.split(data)]
    test_size = splits[0][1].shape[0]

    model = sm.tsa.statespace.SARIMAX(data, order=(1, 0, 0))

    y_train = data.iloc[splits[0][0]]
    y_test = data.iloc[splits[0][1]]
    model_cv = sm.tsa.statespace.SARIMAX(y_train, order=(1, 0, 0))
    results_cv = model_cv.fit(maxiter=5000)
    pred_test = results_cv.predict(start=0, end=len(y_train)+test_size-1, dynamic=False)[-test_size:]
    print(mean_squared_error(y_test, pred_test))
    split_0_y.append(y_test.y)
    split_0_preds.append(pred_test)


    y_train = data.iloc[splits[1][0]]
    y_test = data.iloc[splits[1][1]]
    model_cv = sm.tsa.statespace.SARIMAX(y_train, order=(1, 0, 0))
    results_cv = model_cv.fit(maxiter=5000)
    pred_test = results_cv.predict(start=0, end=len(y_train)+test_size-1, dynamic=False)[-test_size:]
    split_1_y.append(y_test.y)
    split_1_preds.append(pred_test)



    y_train = data.iloc[splits[2][0]]
    y_test = data.iloc[splits[2][1]]
    model_cv = sm.tsa.statespace.SARIMAX(y_train, order=(1, 0, 0))
    results_cv = model_cv.fit(maxiter=5000)
    pred_test = results_cv.predict(start=0, end=len(y_train)+test_size-1, dynamic=False)[-test_size:]
    split_2_y.append(y_test.y)
    split_2_preds.append(pred_test)

Large Magellanic Cloud (LMC)
2.250789737638028e-09


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:219: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  ' ignored when e.g. forecasting.', ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/base/model.py:512: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  "Check mle_retvals", ConvergenceWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/st

In [55]:
len(split_0_y)

1

In [56]:
split_0_preds

[1994-01-01    0.050130
 1996-01-01    0.049789
 1998-01-01    0.049450
 2000-01-01    0.049113
 Freq: 2AS-JAN, dtype: float64]

In [61]:
mses = []

mses.append(mean_squared_error(split_0_y, split_0_preds))
mses.append(mean_squared_error(split_1_y, split_1_preds))
mses.append(mean_squared_error(split_2_y, split_2_preds))

mses
print(np.mean(mses))

3.604368608365351e-05


In [125]:
#Fitting time series on each galaxy


#Train and test set

#df_combined['preds'] = df_combined['y'].apply(lambda x:0)

pd.reset_option('display.max_rows')


order_updated = (1, 0, 1)

results_df = pd.DataFrame(columns=['date','y','preds','galaxy','galactic year 1'])
error_list = []
split_1_y = []
split_2_y = []
split_0_y = []
split_1_preds = []
split_2_preds = []
split_0_preds = []

for g in df.galaxy.unique():
    try:
        print(g)
        df_temp = df[df['galaxy']==g].copy()
        df_temp.sort_values("galactic year 1",inplace=True)
#             df_temp['galactic year'] = df_temp['galactic year'].apply(lambda x:(np.round((x/1000),0))*2)
#             df_temp['galactic year'] = df_temp['galactic year'].astype('int64')
#             df_temp['galactic year'] = df_temp['galactic year'].astype('str')
#             df_temp['galactic year'] = df_temp['galactic year'] + "0101"
#             df_temp['date'] = pd.to_datetime(df_temp['galactic year'], yearfirst=True
#                                              , format='%Y/%m/%d'
#                                             )

        df_temp_temp = df_temp[['date','y','galaxy','galactic year 1']]
        df_temp_temp_1 = df_temp_temp[['date','y']].copy()
        df_temp_temp_1.set_index('date', inplace=True, drop=True)
        data = df_temp_temp_1

        ts = TimeSeriesSplit(n_splits=3)
        splits = [split for split in ts.split(data)]
        test_size = splits[0][1].shape[0]

        model = sm.tsa.statespace.SARIMAX(data, order=order_updated)

        y_train = data.iloc[splits[0][0]]
        y_test = data.iloc[splits[0][1]]
        model_cv = sm.tsa.statespace.SARIMAX(y_train, order=order_updated)
        results_cv = model_cv.fit(maxiter=5000)
        pred_test = results_cv.predict(start=0, end=len(y_train)+test_size-1, dynamic=False)[-test_size:]
        print(mean_squared_error(y_test, pred_test))
        for x in y_test.y:
            split_0_y.append(x)
        for x in pred_test:
            split_0_preds.append(x)


        y_train = data.iloc[splits[1][0]]
        y_test = data.iloc[splits[1][1]]
        model_cv = sm.tsa.statespace.SARIMAX(y_train, order=order_updated)
        results_cv = model_cv.fit(maxiter=5000)
        pred_test = results_cv.predict(start=0, end=len(y_train)+test_size-1, dynamic=False)[-test_size:]
        for z in y_test.y:
            split_1_y.append(z)
        for z in pred_test:
            split_1_preds.append(z)



        y_train = data.iloc[splits[2][0]]
        y_test = data.iloc[splits[2][1]]
        model_cv = sm.tsa.statespace.SARIMAX(y_train, order=order_updated)
        results_cv = model_cv.fit(maxiter=5000)
        pred_test = results_cv.predict(start=0, end=len(y_train)+test_size-1, dynamic=False)[-test_size:]
        for a in y_test.y:
            split_2_y.append(a)
        for a in pred_test:
            split_2_preds.append(a)


    except:
        None
        print('ERROR:',g)
        error_list.append(g)
#             df_temp = df[df['galaxy']==g].copy()
#             df = df[~(df['galaxy']==g)]
#             df_temp.sort_values("galactic year",inplace=True)
#             df_temp['preds'] = df_temp['y']
#             df = pd.concat([df,df_temp])
print(error_list)

    
    


Large Magellanic Cloud (LMC)
4.562832383176583e-08


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:219: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  ' ignored when e.g. forecasting.', ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/base/model.py:512: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  "Check mle_retvals", ConvergenceWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/st

Camelopardalis B
1.621687352223565e-07


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/base/model.py:512: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  "Check mle_retvals", ConvergenceWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:219: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  ' ignored when e.g. forecasting.', ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/st

Virgo I
5.975739328696619e-06


...

NGC 5206
4.1036840464318455e-06


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:219: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  ' ignored when e.g. forecasting.', ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsm

NGC 5102
3.432554131997273e-06


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/statespace/sarimax.py:949: UserWarning: Non-stationary starting autoregressive parameters found. Using zeros as starting parameters.
  warn('Non-stationary starting autoregressive parameters'
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)


['NGC 5253']


In [118]:
split_1_y

[0.04831394667096667,
 0.047988210823426636,
 0.047607099434787366,
 0.04739223757115285,
 0.057700450904955125,
 0.05790786805376402,
 0.05766313168671821,
 0.056803310730746966,
 0.05665627727628144,
 0.042872955794906235,
 0.04246116050721782,
 0.04223587128183148,
 0.04187490287694684,
 0.04042700639692631,
 0.04006004667116092,
 0.042353110763136304,
 0.04191958282654129,
 0.041654622451142265,
 0.04125751742670525,
 0.03906729442321455,
 0.038659426169705864,
 0.17643830511053638,
 0.17713772304222794,
 0.18660570069432814,
 0.18755680357709315,
 0.1878053117445764,
 0.1881255199668651,
 0.04524263631203906,
 0.04480688650501663,
 0.04438051495034945,
 0.04410695239921747,
 0.04371324286565581,
 0.0489554368291304,
 0.04859092551907662,
 0.04824809563634491,
 0.04783515900820856,
 0.047617765443418884,
 0.04713391520343047,
 0.056578128682776674,
 0.0561662959948267,
 0.055934338441882565,
 0.05562964746686927,
 0.05379468842254676,
 0.053510800541836434,
 0.046040653659819575,
 

In [121]:
# (p,d,q)=(0,0,0)

rmses = []

rmses.append(mean_squared_error(split_0_y, split_0_preds, squared=False))
rmses.append(mean_squared_error(split_1_y, split_1_preds, squared=False))
rmses.append(mean_squared_error(split_2_y, split_2_preds, squared=False))

print(rmses)
print(np.mean(rmses))

[0.099220578970572, 0.10247648281240321, 0.11944302609203085]
0.10704669595833534


In [116]:
#(1,1,0)

rmses = []

rmses.append(mean_squared_error(split_0_y, split_0_preds, squared=False))
rmses.append(mean_squared_error(split_1_y, split_1_preds, squared=False))
rmses.append(mean_squared_error(split_2_y, split_2_preds, squared=False))

print(rmses)
print(np.mean(rmses))

[0.0032529323196517743, 0.003949890099708338, 0.033219630858886344]
0.01347415109274882


In [123]:
#(1,0,1)

rmses = []

rmses.append(mean_squared_error(split_0_y, split_0_preds, squared=False))
rmses.append(mean_squared_error(split_1_y, split_1_preds, squared=False))
rmses.append(mean_squared_error(split_2_y, split_2_preds, squared=False))

print(rmses)
print(np.mean(rmses))

[0.0033956833146390327, 0.004662256149841478, 0.03231765974247019]
0.013458533068983565


In [119]:
# (p,d,q)=(1,0,0)

rmses = []

rmses.append(mean_squared_error(split_0_y, split_0_preds, squared=False))
rmses.append(mean_squared_error(split_1_y, split_1_preds, squared=False))
rmses.append(mean_squared_error(split_2_y, split_2_preds, squared=False))

print(rmses)
print(np.mean(rmses))

[0.0036084696918581077, 0.00392070600476079, 0.03185094788864337]
0.013126707861754091


In [76]:
len(split_2_y)
len(split_2_preds)

897

In [78]:
df[df['galaxy']=='NGC 5253']

Adjusted net savings   \
144              20.751377   

     Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
144                                         114.074664                      

     Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
144                                           6.313144                           

     Current health expenditure (% of GGP)  \
144                               8.536079   

     Domestic credit provided by financial sector (% of GGP)  Education Index  \
144                                         119.963809               0.750846   

     Employment in agriculture (% of total employment)  \
144                                          55.203046   

     Employment in services (% of total employment)  \
144                                       67.082939   

     Employment to population ratio (% ages 15 and older)  \
144                                          69.150998      

     Estimated gross galactic income per capita, female  ...  \
144                                       22013.091432   ...   

     Vulnerable employment (% of total employment)  \
144                                      69.460892   

     Young age (0-14) dependency ratio (per 100 creatures ages 15-64)  \
144                                          79.295416                  

     Youth unemployment rate (female to male ratio)  \
144                                        2.257781   

     existence expectancy at birth  existence expectancy index  galactic year  \
144                      77.382893                    0.882087         990025   

       galaxy         y  galactic year 1       date  
144  NGC 5253  0.045115         19800101 1980-01-01  

[1 rows x 82 columns]

# Time Series - just for y - modelling


In [126]:
#Loading in combined train and test set

df = pd.read_csv('train.csv')
df_test = pd.read_csv('test.csv')

df["train_test"] = 'train'
df_test["train_test"] = "test"

df_combined = pd.concat([df,df_test])


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:9: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  if __name__ == '__main__':


In [127]:
#Linear interpolation on all features

def interpolator(df):
    for g in df.galaxy.unique():
        #splitting out the individual galaxies
        df_temp = df[df['galaxy']==g].copy()
        df = df[~(df['galaxy']==g)]
        #filling the Nans (first with interpolation and then backfilling if missing for start)
        df_temp.sort_values("galactic year",inplace=True)
        df_temp.interpolate(method='linear',inplace=True)
        df_temp.fillna(method ='bfill',inplace=True)
        df_temp.fillna(method ='ffill',inplace=True)
        #adding back to dataframe
        df = pd.concat([df,df_temp])
    #filling the Nans for any which didnt have anything to fill at all
    df.fillna(df.mean(),inplace=True)
    return df

df_combined = interpolator(df_combined)
#df_combined = pd.get_dummies(df_combined, columns=['galaxy'])
df = df_combined[df_combined["train_test"]=='train'].copy()
df_test = df_combined[df_combined["train_test"]=='test'].copy()
df.drop('train_test',axis=1,inplace=True)
df_test.drop('train_test',axis=1,inplace=True)


In [128]:
df.head()

Adjusted net savings   \
0                43.391708   
194              43.391708   
410              43.391708   
543              43.391708   
765              43.391708   

     Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
0                                           174.617899                      
194                                         165.945907                      
410                                         157.273915                      
543                                         148.601923                      
765                                         139.929931                      

     Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
0                                             6.313144                           
194                                           6.313144                           
410                                           6.313144                           
543                                           6.313144                           
765                                           6.313144                           

     Current health expenditure (% of GGP)  \
0                                 6.248891   
194                               6.248891   
410                               6.248891   
543                               6.248891   
765                               6.248891   

     Domestic credit provided by financial sector (% of GGP)  Education Index  \
0                                            75.604799               0.526375   
194                                          73.837393               0.526375   
410                                          72.069987               0.526375   
543                                          70.302580               0.526375   
765                                          68.535174               0.526375   

     Employment in agriculture (% of total employment)  \
0                                            96.827657   
194                                          96.827657   
410                                          95.022335   
543                                          93.217014   
765                                          91.411692   

     Employment in services (% of total employment)  \
0                                         53.392606   
194                                       53.392606   
410                                       50.937661   
543                                       48.482717   
765                                       46.027772   

     Employment to population ratio (% ages 15 and older)  \
0                                            76.506783      
194                                          76.506783      
410                                          76.302787      
543                                          76.098791      
765                                          75.894795      

     Estimated gross galactic income per capita, female  ...  \
0                                         16498.415777   ...   
194                                       16498.415777   ...   
410                                       16498.415777   ...   
543                                       16498.415777   ...   
765                                       16498.415777   ...   

     Unemployment, total (% of labour force)  \
0                                   6.682524   
194                                 6.682524   
410                                 6.879042   
543                                 7.075560   
765                                 7.272077   

     Unemployment, youth (% ages 15–24)  \
0                             21.261283   
194                           21.261283   
410                           21.365068   
543                           21.468853   
765                           21.572638   

     Vulnerable employment (% of total employment)  \
0                                        91.911151   
194             

In [129]:
#Creating copy of combined dataset with reset index

df_combined_1 = df_combined.copy()
df_combined_1.reset_index(inplace=True,drop=False)
df_combined_1.drop("index", axis=1, inplace=True)
df_combined_1

Adjusted net savings   \
0                 43.391708   
1                 43.391708   
2                 43.391708   
3                 43.391708   
4                 43.391708   
...                     ...   
4750              15.240960   
4751              17.145098   
4752              19.753047   
4753               9.882289   
4754              22.494515   

      Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
0                                            174.617899                      
1                                            165.945907                      
2                                            157.273915                      
3                                            148.601923                      
4                                            139.929931                      
...                                                 ...                      
4750                                          82.856607                      
4751                                          72.740861                      
4752                                          70.451838                      
4753                                          77.275835                      
4754                                          77.336714                      

      Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
0                                              6.313144                           
1                                              6.313144                           
2                                              6.313144                           
3                                              6.313144                           
4                                              6.313144                           
...                                                 ...                           
4750                                           6.313144                           
4751                                           6.313144                           
4752                                           6.313144                           
4753                                           6.313144                           
4754                                           6.313144                           

      Current health expenditure (% of GGP)  \
0                                  6.248891   
1                                  6.248891   
2                                  6.248891   
3                                  6.248891   
4                                  6.248891   
...                                     ...   
4750                              10.437331   
4751                              11.107914   
4752                              13.665476   
4753                              12.899332   
4754                              13.761286   

      Domestic credit provided by financial sector (% of GGP)  \
0                                             75.604799         
1                                             73.837393         
2                                             72.069987         
3                                             70.302580         
4                                             68.535174         
...                                                 ...         
4750                                         235.956289         
4751                                         269.195714         
4752                                         281.704506         
4753                                         223.423437         
4754                                         212.539861         

      Education Index  Employment in agriculture (% of total employment)  \
0            0.526375                                          96.827657   
1            0.526375                                          96.827657   
2            0.526375                                          95.022335   
3            0.526375                            

In [130]:
for n in df_combined_1.index:
    
    if df_combined_1["train_test"].loc[n]=='test':
        df_combined_1['y'].loc[n] = np.nan
        
    else:
        df_combined_1['y'].loc[n] = df_combined_1['y'].loc[n]
        
df_combined_1['y']

df_combined['y'] = list(df_combined_1['y'])

/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:205: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)


In [131]:
#Fitting galactic year to date time format

df_combined['galactic year 1'] = df_combined['galactic year'].apply(lambda x:(np.round((x/1000),0))*2)
df_combined['galactic year 1'] = df_combined['galactic year 1'].astype('int64')
df_combined['galactic year 1'] = df_combined['galactic year 1'].astype('str')
df_combined['galactic year 1'] = df_combined['galactic year 1'] + "0101"
df_combined['date'] = pd.to_datetime(df_combined['galactic year 1'], yearfirst=True
                                 , format='%Y/%m/%d'
                                )
df_combined.head()

Adjusted net savings   \
0                43.391708   
194              43.391708   
410              43.391708   
543              43.391708   
765              43.391708   

     Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
0                                           174.617899                      
194                                         165.945907                      
410                                         157.273915                      
543                                         148.601923                      
765                                         139.929931                      

     Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
0                                             6.313144                           
194                                           6.313144                           
410                                           6.313144                           
543                                           6.313144                           
765                                           6.313144                           

     Current health expenditure (% of GGP)  \
0                                 6.248891   
194                               6.248891   
410                               6.248891   
543                               6.248891   
765                               6.248891   

     Domestic credit provided by financial sector (% of GGP)  Education Index  \
0                                            75.604799               0.526375   
194                                          73.837393               0.526375   
410                                          72.069987               0.526375   
543                                          70.302580               0.526375   
765                                          68.535174               0.526375   

     Employment in agriculture (% of total employment)  \
0                                            96.827657   
194                                          96.827657   
410                                          95.022335   
543                                          93.217014   
765                                          91.411692   

     Employment in services (% of total employment)  \
0                                         53.392606   
194                                       53.392606   
410                                       50.937661   
543                                       48.482717   
765                                       46.027772   

     Employment to population ratio (% ages 15 and older)  \
0                                            76.506783      
194                                          76.506783      
410                                          76.302787      
543                                          76.098791      
765                                          75.894795      

     Estimated gross galactic income per capita, female  ...  \
0                                         16498.415777   ...   
194                                       16498.415777   ...   
410                                       16498.415777   ...   
543                                       16498.415777   ...   
765                                       16498.415777   ...   

     Young age (0-14) dependency ratio (per 100 creatures ages 15-64)  \
0                                            98.216072                  
194                                          95.964868                  
410                                          93.713664                  
543                                          91.462460                  
765                                          89.211257                  

     Youth unemployment rate (female to male ratio)  \
0                                          2.184798   
194                                        2.184798   
410                                        2.114685   
543          

In [ ]:
#Fitting time series on each galaxy


#Train and test set

#df_combined['preds'] = df_combined['y'].apply(lambda x:0)

pd.reset_option('display.max_rows')


order_updated = (1, 1, 0)

results_df = pd.DataFrame(columns=['date','y','preds','galaxy','galactic year 1','train_test'])
error_list = []


for g in df.galaxy.unique():
    try:
        print(g)
        df_temp = df_combined[df_combined['galaxy']==g].copy()
        df_temp.sort_values("galactic year 1",inplace=True)

        df_temp_temp = df_temp[['date','y','galaxy','galactic year 1','train_test']]
        df_temp_temp_1 = df_temp_temp[['date','y']].copy()
        df_temp_temp_1.set_index('date', inplace=True, drop=True)
        data = df_temp_temp_1

        ts = TimeSeriesSplit(n_splits=3)
        splits = [split for split in ts.split(data)]
        test_size = splits[0][1].shape[0]

        model = sm.tsa.statespace.SARIMAX(data, order=order_updated)

        

    except:
        None
        print('ERROR:',g)
        error_list.append(g)
#             df_temp = df[df['galaxy']==g].copy()
#             df = df[~(df['galaxy']==g)]
#             df_temp.sort_values("galactic year",inplace=True)
#             df_temp['preds'] = df_temp['y']
#             df = pd.concat([df,df_temp])
print(error_list)

    
    


In [138]:
#Fitting time series on each galaxy


#Train and test set




results_df = pd.DataFrame(columns=['date','y','preds','galaxy','train_test','galactic year 1'])
error_list = []

for g in df_combined.galaxy.unique():
    try:
        print(g)
        df_temp = df_combined[df_combined['galaxy']==g].copy()
        df = df_combined[~(df_combined['galaxy']==g)]
        df_temp.sort_values("galactic year 1",inplace=True)
#             df_temp['galactic year'] = df_temp['galactic year'].apply(lambda x:(np.round((x/1000),0))*2)
#             df_temp['galactic year'] = df_temp['galactic year'].astype('int64')
#             df_temp['galactic year'] = df_temp['galactic year'].astype('str')
#             df_temp['galactic year'] = df_temp['galactic year'] + "0101"
#             df_temp['date'] = pd.to_datetime(df_temp['galactic year'], yearfirst=True
#                                              , format='%Y/%m/%d'
#                                             )

        df_temp_temp = df_temp[['date','y','galaxy','train_test','galactic year 1']]
        df_temp_temp_1 = df_temp_temp[['date','y']].copy()
        df_temp_temp_1.set_index('date', inplace=True, drop=True)
        data = df_temp_temp_1
        model = sm.tsa.statespace.SARIMAX(data, order=(1, 0, 0))
        results = model.fit(maxiter=5000)

        #option 1
        df_temp_temp['preds'] = list(results.fittedvalues)


        results_df = pd.concat([results_df,df_temp_temp])



#             print(results_df)
#         df = pd.concat([df,df_temp])
    except:
        None
        print('ERROR:',g)
        error_list.append(g)
#             df_temp = df[df['galaxy']==g].copy()
#             df = df[~(df['galaxy']==g)]
#             df_temp.sort_values("galactic year",inplace=True)
#             df_temp['preds'] = df_temp['y']
#             df = pd.concat([df,df_temp])
print(error_list)






Large Magellanic Cloud (LMC)
Camelopardalis B
Virgo I
UGC 8651 (DDO 181)
Tucana Dwarf


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:37: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/t

KKh 060
Grus II
UGCA 292


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/base/model.py:512: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  "Check mle_retvals", ConvergenceWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)


Aquarius II
Andromeda XI
Antlia Dwarf
IC 1613 (UGC 668)


...

/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency informati

Leo I Dwarf (DDO 74, UGC 5470)
UGC 8508 (I Zw 060)


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)


NGC 5237
NGC 5206
NGC 5102
['NGC 5253']


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/base/model.py:512: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  "Check mle_retvals", ConvergenceWarning)


In [139]:
results_df

date galactic year 1                        galaxy     preds  \
0    1980-01-01        19800101  Large Magellanic Cloud (LMC)  0.000000   
194  1982-01-01        19820101  Large Magellanic Cloud (LMC)  0.051369   
410  1984-01-01        19840101  Large Magellanic Cloud (LMC)  0.050905   
543  1986-01-01        19860101  Large Magellanic Cloud (LMC)  0.050799   
765  1988-01-01        19880101  Large Magellanic Cloud (LMC)  0.050476   
...         ...             ...                           ...       ...   
3512 2024-01-01        20240101                      NGC 5102  0.166088   
3610 2026-01-01        20260101                      NGC 5102  0.176647   
771  2028-01-01        20280101                      NGC 5102  0.182948   
812  2030-01-01        20300101                      NGC 5102  0.182919   
616  2032-01-01        20320101                      NGC 5102  0.182889   

     train_test         y  
0         train  0.052590  
194       train  0.052115  
410       train  0.052006  
543       train  0.051675  
765       train  0.051334  
...         ...       ...  
3512      train  0.176675  
3610      train  0.182978  
771        test       NaN  
812        test       NaN  
616        test       NaN  

[4754 rows x 6 columns]

In [141]:
results_df_test = results_df[results_df['train_test']=='test']
results_df_test.sort_index()

date galactic year 1                galaxy     preds train_test   y
0   2014-01-01        20140101               KK98 77  0.040718       test NaN
1   2014-01-01        20140101         Reticulum III  0.038930       test NaN
2   2016-01-01        20160101         Reticulum III  0.038879       test NaN
3   2014-01-01        20140101               Segue 1  0.038703       test NaN
4   2026-01-01        20260101               Virgo I  0.029106       test NaN
..         ...             ...                   ...       ...        ...  ..
885 2032-01-01        20320101  ESO 383-087 (ISG 39)  0.024083       test NaN
886 2032-01-01        20320101               NGC 247  0.028439       test NaN
887 2032-01-01        20320101            ESO 325-11  0.063985       test NaN
888 2032-01-01        20320101           ESO 540-032  0.056399       test NaN
889 2032-01-01        20320101               KK98 77  0.023769       test NaN

[890 rows x 6 columns]

In [145]:
results_df_test_1 = results_df_test.sort_index()
#results_df_test_1.to_csv('time_series_y_test_preds.csv', index=False)

In [144]:
pd.read_csv('test.csv')

galactic year                galaxy  existence expectancy index  \
0          1007012               KK98 77                    0.456086   
1          1007012         Reticulum III                    0.529835   
2          1008016         Reticulum III                    0.560976   
3          1007012               Segue 1                    0.565910   
4          1013042               Virgo I                    0.588274   
..             ...                   ...                         ...   
885        1016064  ESO 383-087 (ISG 39)                         NaN   
886        1016064               NGC 247                         NaN   
887        1016064            ESO 325-11                         NaN   
888        1016064           ESO 540-032                         NaN   
889        1016064               KK98 77                         NaN   

     existence expectancy at birth  Gross income per capita  Income Index  \
0                        51.562543             12236.576447      0.593325   
1                        57.228262              3431.883825      0.675407   
2                        59.379539             27562.914252      0.594624   
3                        59.952390             20352.232905      0.837700   
4                        55.428320             23959.704016      0.520579   
..                             ...                      ...           ...   
885                            NaN                      NaN           NaN   
886                            NaN                      NaN           NaN   
887                            NaN                      NaN           NaN   
888                            NaN                      NaN           NaN   
889                            NaN                      NaN           NaN   

     Expected years of education (galactic years)  \
0                                       10.414164   
1                                        7.239485   
2                                       11.774890   
3                                       11.613621   
4                                       10.392416   
..                                            ...   
885                                           NaN   
886                                           NaN   
887                                           NaN   
888                                           NaN   
889                                           NaN   

     Mean years of education (galactic years)  \
0                                   10.699072   
1                                    5.311122   
2                                    5.937797   
3                                   10.067882   
4                                    6.374637   
..                                        ...   
885                                       NaN   
886                                       NaN   
887                                       NaN   
888                                       NaN   
889                                       NaN   

     Intergalactic Development Index (IDI)  Education Index  ...  \
0                                 0.547114         0.556267  ...   
1                                 0.497688         0.409969  ...   
2                                 0.544744         0.486167  ...   
3                                 0.691641         0.523441  ...   
4                                 0.530676         0.580418  ...   
..                                     ...              ...  ...   
885                                    NaN              NaN  ...   
886                                    NaN              NaN  ...   
887                                    NaN              NaN  ...   
888                                    NaN              NaN  ...   
889                                    NaN              NaN  ...   

     Current health expenditure (% of GGP)  \
0                                      NaN   
1                                      NaN   
2                                 

In [136]:
#Fitting time series on each galaxy - TESTING ON LARGE MAGELLANIC CLOUD


#Train and test set




results_df = pd.DataFrame(columns=['date','y','preds','galaxy','train_test','galactic year 1'])
error_list = []

for g in df_combined.galaxy.unique()[:1]:
    
    print(g)
    df_temp = df_combined[df_combined['galaxy']==g].copy()
    df = df_combined[~(df_combined['galaxy']==g)]
    df_temp.sort_values("galactic year 1",inplace=True)
#             df_temp['galactic year'] = df_temp['galactic year'].apply(lambda x:(np.round((x/1000),0))*2)
#             df_temp['galactic year'] = df_temp['galactic year'].astype('int64')
#             df_temp['galactic year'] = df_temp['galactic year'].astype('str')
#             df_temp['galactic year'] = df_temp['galactic year'] + "0101"
#             df_temp['date'] = pd.to_datetime(df_temp['galactic year'], yearfirst=True
#                                              , format='%Y/%m/%d'
#                                             )

    df_temp_temp = df_temp[['date','y','galaxy','train_test','galactic year 1']]
    df_temp_temp_1 = df_temp_temp[['date','y']].copy()
    df_temp_temp_1.set_index('date', inplace=True, drop=True)
    data = df_temp_temp_1
    model = sm.tsa.statespace.SARIMAX(data, order=(1, 0, 0))
    results = model.fit(maxiter=5000)

    #option 1
    df_temp_temp['preds'] = list(results.fittedvalues)

    #option 2
    print(len(df_temp_temp['date']))
    print(len(list(results.predict(start=0, end=len(data)-1, dynamic=False))))
#     df_temp_temp['preds'] = list(results.predict(start=0, end=len(data)-1, dynamic=False))
    
    #option 3
#     df_temp_temp['preds'] = list(results.predict(start=data.index[0], end=data.index[-1], dynamic=False))




#             print(df_temp_temp.preds)
#             print(list(results.fittedvalues))
#             print(len(list(results.fittedvalues)))
#             print(len(df_temp['y']))


#             for n in df_temp_temp.index:
#                 if df_temp_temp['preds'].loc[n]==0:
#                     df_temp_temp['preds'].loc[n]=np.nan
#                 else:
#                     df_temp_temp['preds'].loc[n]=df_temp_temp['preds'].loc[n]
#             df_temp_temp.preds.fillna(method='bfill',inplace=True)
#             df_temp_temp.preds.fillna(method='ffill',inplace=True)


Large Magellanic Cloud (LMC)
27
27


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [107]:
data.index[-1]

Timestamp('2032-01-01 00:00:00')

In [133]:
#Option 3 of predicting

df_temp_temp

date         y                        galaxy train_test  \
0    1980-01-01  0.052590  Large Magellanic Cloud (LMC)      train   
194  1982-01-01  0.052115  Large Magellanic Cloud (LMC)      train   
410  1984-01-01  0.052006  Large Magellanic Cloud (LMC)      train   
543  1986-01-01  0.051675  Large Magellanic Cloud (LMC)      train   
765  1988-01-01  0.051334  Large Magellanic Cloud (LMC)      train   
1053 1990-01-01  0.051056  Large Magellanic Cloud (LMC)      train   
1244 1992-01-01  0.050473  Large Magellanic Cloud (LMC)      train   
1411 1994-01-01  0.050179  Large Magellanic Cloud (LMC)      train   
1570 1996-01-01  0.049803  Large Magellanic Cloud (LMC)      train   
1758 1998-01-01  0.049484  Large Magellanic Cloud (LMC)      train   
1833 2000-01-01  0.049185  Large Magellanic Cloud (LMC)      train   
2015 2002-01-01  0.048314  Large Magellanic Cloud (LMC)      train   
2274 2004-01-01  0.047988  Large Magellanic Cloud (LMC)      train   
2421 2006-01-01  0.047607  Large Magellanic Cloud (LMC)      train   
2611 2008-01-01  0.047392  Large Magellanic Cloud (LMC)      train   
2846 2010-01-01  0.047043  Large Magellanic Cloud (LMC)      train   
2891 2012-01-01  0.046172  Large Magellanic Cloud (LMC)      train   
309  2014-01-01       NaN  Large Magellanic Cloud (LMC)       test   
144  2016-01-01       NaN  Large Magellanic Cloud (LMC)       test   
238  2018-01-01       NaN  Large Magellanic Cloud (LMC)       test   
375  2020-01-01       NaN  Large Magellanic Cloud (LMC)       test   
422  2022-01-01       NaN  Large Magellanic Cloud (LMC)       test   
256  2024-01-01       NaN  Large Magellanic Cloud (LMC)       test   
3679 2026-01-01  0.031641  Large Magellanic Cloud (LMC)      train   
3770 2028-01-01  0.031360  Large Magellanic Cloud (LMC)      train   
160  2030-01-01       NaN  Large Magellanic Cloud (LMC)       test   
322  2032-01-01       NaN  Large Magellanic Cloud (LMC)       test   

     galactic year 1     preds  
0           19800101  0.000000  
194         19820101  0.051369  
410         19840101  0.050905  
543         19860101  0.050799  
765         19880101  0.050476  
1053        19900101  0.050142  
1244        19920101  0.049871  
1411        19940101  0.049301  
1570        19960101  0.049014  
1758        19980101  0.048647  
1833        20000101  0.048336  
2015        20020101  0.048044  
2274        20040101  0.047192  
2421        20060101  0.046874  
2611        20080101  0.046502  
2846        20100101  0.046292  
2891        20120101  0.045951  
309         20140101  0.045100  
144         20160101  0.044053  
238         20180101  0.043031  
375         20200101  0.042032  
422         20220101  0.041056  
256         20240101  0.040103  
3679        20260101  0.039172  
3770        20280101  0.030907  
160         20300101  0.030632  
322         20320101  0.029921

In [135]:
#Option 2 of predicting

df_temp_temp

date         y                        galaxy train_test  \
0    1980-01-01  0.052590  Large Magellanic Cloud (LMC)      train   
194  1982-01-01  0.052115  Large Magellanic Cloud (LMC)      train   
410  1984-01-01  0.052006  Large Magellanic Cloud (LMC)      train   
543  1986-01-01  0.051675  Large Magellanic Cloud (LMC)      train   
765  1988-01-01  0.051334  Large Magellanic Cloud (LMC)      train   
1053 1990-01-01  0.051056  Large Magellanic Cloud (LMC)      train   
1244 1992-01-01  0.050473  Large Magellanic Cloud (LMC)      train   
1411 1994-01-01  0.050179  Large Magellanic Cloud (LMC)      train   
1570 1996-01-01  0.049803  Large Magellanic Cloud (LMC)      train   
1758 1998-01-01  0.049484  Large Magellanic Cloud (LMC)      train   
1833 2000-01-01  0.049185  Large Magellanic Cloud (LMC)      train   
2015 2002-01-01  0.048314  Large Magellanic Cloud (LMC)      train   
2274 2004-01-01  0.047988  Large Magellanic Cloud (LMC)      train   
2421 2006-01-01  0.047607  Large Magellanic Cloud (LMC)      train   
2611 2008-01-01  0.047392  Large Magellanic Cloud (LMC)      train   
2846 2010-01-01  0.047043  Large Magellanic Cloud (LMC)      train   
2891 2012-01-01  0.046172  Large Magellanic Cloud (LMC)      train   
309  2014-01-01       NaN  Large Magellanic Cloud (LMC)       test   
144  2016-01-01       NaN  Large Magellanic Cloud (LMC)       test   
238  2018-01-01       NaN  Large Magellanic Cloud (LMC)       test   
375  2020-01-01       NaN  Large Magellanic Cloud (LMC)       test   
422  2022-01-01       NaN  Large Magellanic Cloud (LMC)       test   
256  2024-01-01       NaN  Large Magellanic Cloud (LMC)       test   
3679 2026-01-01  0.031641  Large Magellanic Cloud (LMC)      train   
3770 2028-01-01  0.031360  Large Magellanic Cloud (LMC)      train   
160  2030-01-01       NaN  Large Magellanic Cloud (LMC)       test   
322  2032-01-01       NaN  Large Magellanic Cloud (LMC)       test   

     galactic year 1     preds  
0           19800101  0.000000  
194         19820101  0.051369  
410         19840101  0.050905  
543         19860101  0.050799  
765         19880101  0.050476  
1053        19900101  0.050142  
1244        19920101  0.049871  
1411        19940101  0.049301  
1570        19960101  0.049014  
1758        19980101  0.048647  
1833        20000101  0.048336  
2015        20020101  0.048044  
2274        20040101  0.047192  
2421        20060101  0.046874  
2611        20080101  0.046502  
2846        20100101  0.046292  
2891        20120101  0.045951  
309         20140101  0.045100  
144         20160101  0.044053  
238         20180101  0.043031  
375         20200101  0.042032  
422         20220101  0.041056  
256         20240101  0.040103  
3679        20260101  0.039172  
3770        20280101  0.030907  
160         20300101  0.030632  
322         20320101  0.029921

In [137]:
#Option 1 of predicting

df_temp_temp

date         y                        galaxy train_test  \
0    1980-01-01  0.052590  Large Magellanic Cloud (LMC)      train   
194  1982-01-01  0.052115  Large Magellanic Cloud (LMC)      train   
410  1984-01-01  0.052006  Large Magellanic Cloud (LMC)      train   
543  1986-01-01  0.051675  Large Magellanic Cloud (LMC)      train   
765  1988-01-01  0.051334  Large Magellanic Cloud (LMC)      train   
1053 1990-01-01  0.051056  Large Magellanic Cloud (LMC)      train   
1244 1992-01-01  0.050473  Large Magellanic Cloud (LMC)      train   
1411 1994-01-01  0.050179  Large Magellanic Cloud (LMC)      train   
1570 1996-01-01  0.049803  Large Magellanic Cloud (LMC)      train   
1758 1998-01-01  0.049484  Large Magellanic Cloud (LMC)      train   
1833 2000-01-01  0.049185  Large Magellanic Cloud (LMC)      train   
2015 2002-01-01  0.048314  Large Magellanic Cloud (LMC)      train   
2274 2004-01-01  0.047988  Large Magellanic Cloud (LMC)      train   
2421 2006-01-01  0.047607  Large Magellanic Cloud (LMC)      train   
2611 2008-01-01  0.047392  Large Magellanic Cloud (LMC)      train   
2846 2010-01-01  0.047043  Large Magellanic Cloud (LMC)      train   
2891 2012-01-01  0.046172  Large Magellanic Cloud (LMC)      train   
309  2014-01-01       NaN  Large Magellanic Cloud (LMC)       test   
144  2016-01-01       NaN  Large Magellanic Cloud (LMC)       test   
238  2018-01-01       NaN  Large Magellanic Cloud (LMC)       test   
375  2020-01-01       NaN  Large Magellanic Cloud (LMC)       test   
422  2022-01-01       NaN  Large Magellanic Cloud (LMC)       test   
256  2024-01-01       NaN  Large Magellanic Cloud (LMC)       test   
3679 2026-01-01  0.031641  Large Magellanic Cloud (LMC)      train   
3770 2028-01-01  0.031360  Large Magellanic Cloud (LMC)      train   
160  2030-01-01       NaN  Large Magellanic Cloud (LMC)       test   
322  2032-01-01       NaN  Large Magellanic Cloud (LMC)       test   

     galactic year 1     preds  
0           19800101  0.000000  
194         19820101  0.051369  
410         19840101  0.050905  
543         19860101  0.050799  
765         19880101  0.050476  
1053        19900101  0.050142  
1244        19920101  0.049871  
1411        19940101  0.049301  
1570        19960101  0.049014  
1758        19980101  0.048647  
1833        20000101  0.048336  
2015        20020101  0.048044  
2274        20040101  0.047192  
2421        20060101  0.046874  
2611        20080101  0.046502  
2846        20100101  0.046292  
2891        20120101  0.045951  
309         20140101  0.045100  
144         20160101  0.044053  
238         20180101  0.043031  
375         20200101  0.042032  
422         20220101  0.041056  
256         20240101  0.040103  
3679        20260101  0.039172  
3770        20280101  0.030907  
160         20300101  0.030632  
322         20320101  0.029921

# Time series imputing of NaNs

In [1]:
#FINALLY WORKING

df = pd.read_csv('train.csv')
df_test = pd.read_csv('test.csv')
df["train_test"] = 'train'
df_test["train_test"] = "test"

print(df.shape)
print(df_test.shape)

df_combined = pd.concat([df,df_test])
print(df_combined.shape)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

(3865, 81)
(890, 80)


<IPython.core.display.Javascript object>

(4755, 81)


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:11: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  # This is added back by InteractiveShellApp.init_path()


In [2]:
#Creating copy of combined dataset with reset index

df_combined_1 = df_combined.copy()
df_combined_1.reset_index(inplace=True,drop=False)
df_combined_1.drop("index", axis=1, inplace=True)
df_combined_1

Adjusted net savings   \
0                       NaN   
1                 19.177926   
2                 21.151265   
3                       NaN   
4                       NaN   
...                     ...   
4750                    NaN   
4751                    NaN   
4752                    NaN   
4753                    NaN   
4754                    NaN   

      Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
0                                            174.617899                      
1                                            109.892385                      
2                                            230.573666                      
3                                            198.971328                      
4                                             61.008654                      
...                                                 ...                      
4750                                                NaN                      
4751                                                NaN                      
4752                                                NaN                      
4753                                                NaN                      
4754                                                NaN                      

      Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
0                                                   NaN                           
1                                                   NaN                           
2                                              6.534020                           
3                                              5.912194                           
4                                              5.611753                           
...                                                 ...                           
4750                                                NaN                           
4751                                                NaN                           
4752                                                NaN                           
4753                                                NaN                           
4754                                                NaN                           

      Current health expenditure (% of GGP)  \
0                                       NaN   
1                                       NaN   
2                                       NaN   
3                                       NaN   
4                                       NaN   
...                                     ...   
4750                                    NaN   
4751                                    NaN   
4752                                    NaN   
4753                                    NaN   
4754                                    NaN   

      Domestic credit provided by financial sector (% of GGP)  \
0                                             75.604799         
1                                             57.214150         
2                                             76.141735         
3                                                   NaN         
4                                                   NaN         
...                                                 ...         
4750                                                NaN         
4751                                                NaN         
4752                                                NaN         
4753                                                NaN         
4754                                                NaN         

      Education Index  Employment in agriculture (% of total employment)  \
0                 NaN                                                NaN   
1            0.467873                                                NaN   
2            0.363837                                                NaN   
3                 NaN                            

In [ ]:
#Fitting galactic year to date time format

df_combined['galactic year 1'] = df_combined['galactic year'].apply(lambda x:(np.round((x/1000),0))*2)
df_combined['galactic year 1'] = df_combined['galactic year 1'].astype('int64')
df_combined['galactic year 1'] = df_combined['galactic year 1'].astype('str')
df_combined['galactic year 1'] = df_combined['galactic year 1'] + "0101"
df_combined['date'] = pd.to_datetime(df_combined['galactic year 1'], yearfirst=True
                                 , format='%Y/%m/%d'
                                )
df_combined.head()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [215]:
df_combined.head()

Adjusted net savings   \
0                    NaN   
1              19.177926   
2              21.151265   
3                    NaN   
4                    NaN   

   Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
0                                         174.617899                      
1                                         109.892385                      
2                                         230.573666                      
3                                         198.971328                      
4                                          61.008654                      

   Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
0                                                NaN                           
1                                                NaN                           
2                                           6.534020                           
3                                           5.912194                           
4                                           5.611753                           

   Current health expenditure (% of GGP)  \
0                                    NaN   
1                                    NaN   
2                                    NaN   
3                                    NaN   
4                                    NaN   

   Domestic credit provided by financial sector (% of GGP)  Education Index  \
0                                          75.604799                    NaN   
1                                          57.214150               0.467873   
2                                          76.141735               0.363837   
3                                                NaN                    NaN   
4                                                NaN               0.918353   

   Employment in agriculture (% of total employment)  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                                NaN   

   Employment in services (% of total employment)  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   

   Employment to population ratio (% ages 15 and older)  \
0                                                NaN      
1                                                NaN      
2                                                NaN      
3                                                NaN      
4                                                NaN      

   Estimated gross galactic income per capita, female  ...  \
0                                                NaN   ...   
1                                                NaN   ...   
2                                                NaN   ...   
3                                                NaN   ...   
4                                                NaN   ...   

   Young age (0-14) dependency ratio (per 100 creatures ages 15-64)  \
0                                          98.216072                  
1                                          88.322574                  
2                                         114.163995                  
3                                          97.645232                  
4                                          53.835875                  

   Youth unemployment rate (female to male ratio)  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   

   existence expectancy at birth

In [157]:
#Imputing nans with time series

for g in df_combined.galaxy.unique():
    df_temp = df_combined[df_combined['galaxy']==g].copy()
    df = df_combined[~(df_combined['galaxy']==g)]
    #filling the Nans (first with interpolation and then backfilling if missing for start)
    df_temp.sort_values("galactic year",inplace=True)
    df_temp_1 = df_temp.copy()
    df_temp_1.drop(['galaxy','train_test','y',
                    #'galactic year'
                   ],axis=1,inplace=True)
    null_list = [col for col in df_temp_1.columns if df_temp_1[col].isnull().all()]
    for n in null_list:
        df_temp_1.drop(columns=n, axis=1, inplace=True)
    
    
    for p in df_temp_1.columns:
        df_temp_temp_1 = df_temp_temp[['date',p]].copy()
        df_temp_temp_1.set_index('date', inplace=True, drop=True)
        data = df_temp_temp_1
        model = sm.tsa.statespace.SARIMAX(data, order=(1, 0, 0))
        results = model.fit(maxiter=5000)

        #option 1
        
        for q in range(0,df_temp_1[n]):
            if df_temp_1[n].loc[q].isna():
                df_temp_1[n].loc[q] = list(results.fittedvalues)[q]
            else:
                None
                
    for n in null_list:
        df_temp_1[n]=list(df_temp[n])
        df_temp_1['galaxy'] = list(df_temp['galaxy'])
        df_temp_1['train_test'] = list(df_temp['train_test'])
        df_temp_1['y'] = list(df_temp['y'])


        results_df = pd.concat([results_df,df_temp_temp])
    
    df = pd.concat([df,df_temp_1])
#filling the Nans for any which didnt have anything to fill at all
df.fillna(df.mean(),inplace=True)
    



KeyError: "['Adjusted net savings '] not in index"

In [195]:
df_combined['Adjusted net savings ']

0            NaN
1      19.177926
2      21.151265
3            NaN
4            NaN
         ...    
885          NaN
886          NaN
887          NaN
888          NaN
889          NaN
Name: Adjusted net savings , Length: 4755, dtype: float64

In [196]:
df_combined['y'].loc[5]

5    0.052871
5         NaN
Name: y, dtype: float64

In [216]:
#Imputing nans with time series - trying on one galaxy

for g in df_combined.galaxy.unique():
    print(g)
    df_temp = df_combined[df_combined['galaxy']==g].copy()
    df = df_combined[~(df_combined['galaxy']==g)]
    #filling the Nans (first with interpolation and then backfilling if missing for start)
    df_temp.sort_values("galactic year",inplace=True)
    df_temp_1 = df_temp.copy()
    df_temp_1.drop(['galaxy','train_test','y','galactic year 1'
                    #'galactic year'
                   ],axis=1,inplace=True)
    df_temp_1.reset_index(inplace=True)
    null_list = [col for col in df_temp_1.columns if df_temp_1[col].isnull().all()]
    for n in null_list:
        df_temp_1.drop(columns=n, axis=1, inplace=True)
    
    print(null_list)
    
    for p in df_temp_1.columns:
        if p!='date':
            try:
                df_temp_temp_1 = df_temp_1[['date',p]].copy()
                df_temp_temp_1.set_index('date', inplace=True, drop=True)
                data = df_temp_temp_1
                #print(p)
                model = sm.tsa.statespace.SARIMAX(data, order=(1, 0, 0))
                #print("model initiated")
                results = model.fit(maxiter=5000)

                #option 1

                for q in df_temp_1.index:
                    if df_temp_1[p].loc[q]==np.nan:
                        df_temp_1[p].loc[q] = list(results.fittedvalues)[q]
                    else:
                        None
            except:
                #print(p)
                for q in df_temp_1.index:
                    if df_temp_1[p].loc[q]==np.nan:
                        df_temp_1[p].loc[q] = df_temp_1[p].mean()
                    else:
                        None
                    
                
    for n in null_list:
        df_temp_1[n]=list(df_temp[n])
        df_temp_1['galaxy'] = list(df_temp['galaxy'])
        df_temp_1['train_test'] = list(df_temp['train_test'])
        df_temp_1['y'] = list(df_temp['y'])


        results_df = pd.concat([results_df,df_temp_temp])
    
    df = pd.concat([df,df_temp_1])
    
df
#filling the Nans for any which didnt have anything to fill at all
#df.fillna(df.mean(),inplace=True)
    



Large Magellanic Cloud (LMC)
['Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total', 'Private galaxy capital flows (% of GGP)']


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency informati

/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency informati

Camelopardalis B
['Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total']


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency informati

...

/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency informati

NGC 5102
['Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total']


/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency informati

/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency information was provided, so inferred frequency 2AS-JAN will be used.
  % freq, ValueWarning)
/Users/Tiffany/opt/anaconda3/lib/python3.7/site-packages/statsmodels/tsa/base/tsa_model.py:165: ValueWarning: No frequency informati

Adjusted net savings   \
0                     NaN   
1               19.177926   
2               21.151265   
3                     NaN   
4                     NaN   
..                    ...   
22              15.240960   
23              17.145098   
24              19.753047   
25               9.882289   
26              22.494515   

    Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
0                                          174.617899                      
1                                          109.892385                      
2                                          230.573666                      
3                                          198.971328                      
4                                           61.008654                      
..                                                ...                      
22                                          82.856607                      
23                                          72.740861                      
24                                          70.451838                      
25                                          77.275835                      
26                                          77.336714                      

    Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
0                                                 NaN                           
1                                                 NaN                           
2                                            6.534020                           
3                                            5.912194                           
4                                            5.611753                           
..                                                ...                           
22                                                NaN                           
23                                                NaN                           
24                                                NaN                           
25                                                NaN                           
26                                                NaN                           

    Current health expenditure (% of GGP)  \
0                                     NaN   
1                                     NaN   
2                                     NaN   
3                                     NaN   
4                                     NaN   
..                                    ...   
22                              10.437331   
23                              11.107914   
24                              13.665476   
25                              12.899332   
26                              13.761286   

    Domestic credit provided by financial sector (% of GGP)  Education Index  \
0                                           75.604799                    NaN   
1                                           57.214150               0.467873   
2                                           76.141735               0.363837   
3                                                 NaN                    NaN   
4                                                 NaN               0.918353   
..                                                ...                    ...   
22                                         235.956289               1.223794   
23                                         269.195714               1.040462   
24                                         281.704506               1.122439   
25                                         223.423437               1.002551   
26                                         212.539861               1.118854   

    Employment in agriculture (% of total employment)  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3                                      

In [217]:
df

Adjusted net savings   \
0                     NaN   
1               19.177926   
2               21.151265   
3                     NaN   
4                     NaN   
..                    ...   
22              15.240960   
23              17.145098   
24              19.753047   
25               9.882289   
26              22.494515   

    Adolescent birth rate (births per 1,000 female creatures ages 15-19)  \
0                                          174.617899                      
1                                          109.892385                      
2                                          230.573666                      
3                                          198.971328                      
4                                           61.008654                      
..                                                ...                      
22                                          82.856607                      
23                                          72.740861                      
24                                          70.451838                      
25                                          77.275835                      
26                                          77.336714                      

    Creature Immunodeficiency Disease prevalence, adult (% ages 15-49), total  \
0                                                 NaN                           
1                                                 NaN                           
2                                            6.534020                           
3                                            5.912194                           
4                                            5.611753                           
..                                                ...                           
22                                                NaN                           
23                                                NaN                           
24                                                NaN                           
25                                                NaN                           
26                                                NaN                           

    Current health expenditure (% of GGP)  \
0                                     NaN   
1                                     NaN   
2                                     NaN   
3                                     NaN   
4                                     NaN   
..                                    ...   
22                              10.437331   
23                              11.107914   
24                              13.665476   
25                              12.899332   
26                              13.761286   

    Domestic credit provided by financial sector (% of GGP)  Education Index  \
0                                           75.604799                    NaN   
1                                           57.214150               0.467873   
2                                           76.141735               0.363837   
3                                                 NaN                    NaN   
4                                                 NaN               0.918353   
..                                                ...                    ...   
22                                         235.956289               1.223794   
23                                         269.195714               1.040462   
24                                         281.704506               1.122439   
25                                         223.423437               1.002551   
26                                         212.539861               1.118854   

    Employment in agriculture (% of total employment)  \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3                                      

In [211]:
df_temp = df_combined[df_combined['galaxy']=='Lacerta I (Andromeda XXXI)'].copy()
df = df_combined[~(df_combined['galaxy']=='Lacerta I (Andromeda XXXI)')]
#filling the Nans (first with interpolation and then backfilling if missing for start)
df_temp.sort_values("galactic year",inplace=True)
df_temp_1 = df_temp.copy()
df_temp_1.drop(['galaxy','train_test','y','galactic year 1'
                #'galactic year'
               ],axis=1,inplace=True)
df_temp_1.reset_index(inplace=True)


0       18
1      308
2      458
3      693
4      734
5      926
6     1101
7     1370
8     1470
9     1738
10    1857
11    2006
12    2245
13    2417
14    2644
15    2875
16    2930
17     308
18     243
19     218
20     151
21     262
22     390
23     274
24     416
25    3810
Name: index, dtype: int64

In [206]:
df_combined[df_combined['galaxy']=='Lacerta I (Andromeda XXXI)'].index

Int64Index([  18,  308,  458,  693,  734,  926, 1101, 1370, 1470, 1738, 1857,
            2006, 2245, 2417, 2644, 2875, 2930, 3810,  151,  218,  243,  262,
             274,  308,  390,  416],
           dtype='int64')

In [ ]:
#Imputing nans with time series

for g in df.galaxy.unique():
    df_temp = df_combined[df_combined['galaxy']==g].copy()
    df = df_combined[~(df_combined['galaxy']==g)]
    #filling the Nans (first with interpolation and then backfilling if missing for start)
    df_temp.sort_values("galactic year",inplace=True)
    df_temp_1 = df_temp.copy()
    df_temp_1.drop(['galaxy','train_test','y',
                    #'galactic year'
                   ],axis=1,inplace=True)
    null_list = [col for col in df_temp_1.columns if df_temp_1[col].isnull().all()]
    for n in null_list:
        df_temp_1.drop(columns=n, axis=1, inplace=True)
    df_temp_2 = pd.DataFrame(imputer.fit_transform(df_temp_1), columns = df_temp_1.columns)
    for n in null_list:
        df_temp_2[n]=list(df_temp[n])
    df_temp_2['galaxy'] = list(df_temp['galaxy'])
    df_temp_2['train_test'] = list(df_temp['train_test'])
    df_temp_2['y'] = list(df_temp['y'])
    df = pd.concat([df,df_temp_2])
#filling the Nans for any which didnt have anything to fill at all
df.fillna(df.mean(),inplace=True)
    



In [ ]:
df_combined = pd.get_dummies(df_combined, columns=['galaxy'])
df = df_combined[df_combined["train_test"]=='train'].copy()
df_test = df_combined[df_combined["train_test"]=='test'].copy()
df.drop('train_test',axis=1,inplace=True)
df_test.drop('train_test',axis=1,inplace=True)

In [ ]:
df.to_csv('iterative_imputer_df.csv', index=False)
df_test.to_csv('iterative_imputer_df_test.csv', index=False)